# Import Modules

In [54]:
import os, sys
import pandas as pd
import numpy as np
import datetime as dt
from pprint import pprint
import csv
import itertools as it
from prettytable import PrettyTable
# from nanrms import *
# from handover import *
# from mask import *
# from makedir import *
import matplotlib.pylab as plt
import seaborn as sns

pdir = os.path.abspath(os.path.join(os.getcwd(), '..'))  # for jupyter-notebook
sys.path.insert(1, pdir)
from myutils import *

%config InlineBackend.figure_format = 'retina'  # 提高 jupyter notebook 的圖形顯示解析度
# plt.style.use('ggplot')

pd.set_option('display.max_columns', 600)
# pd.set_option('display.max_rows', 200)

first_time = False

datadir = "/Users/jackbedford/Desktop/MOXA/Code/data"
exp = "_Bandlock_Udp_B1_B3_B7_B8_RM500Q"
devices = [
    'qc00',
    # 'qc01',
    'qc02',
    'qc03',
]
schemes = [
    'B1',
    # 'B3',
    'B7',
    'B8',
]
dates = {
    "2023-03-15": [*['#{:02d}'.format(i+1) for i in range(1, 4)], '#06'],
    "2023-03-16": ['#{:02d}'.format(i+1) for i in range(16)],
}

# Collect Data Files

* 跑過第一輪之後就可以註解掉（已存到 pickle files），或將 block 1 的 first_time 改成 False

In [55]:
def set_data(df):
    df['seq'] = df['seq'].astype('Int32')
    df['rpkg'] = df['rpkg'].astype('Int8')
    df['frame_id'] = df['frame_id'].astype('Int32')
    df['Timestamp'] = pd.to_datetime(df['Timestamp'])
    df['xmit_time'] = pd.to_datetime(df['xmit_time'])
    df['arr_time'] = pd.to_datetime(df['arr_time'])
    df['Timestamp_epoch'] = df['Timestamp_epoch'].astype('float32')
    df['xmit_time_epoch'] = df['xmit_time_epoch'].astype('float32')
    df['arr_time_epoch'] = df['arr_time_epoch'].astype('float32')
    df['lost'] = df['lost'].astype('boolean')
    df['excl'] = df['excl'].astype('boolean')
    df['latency'] = df['latency'].astype('float32')
    return df

# RSRP, RSRQ 取值範圍 https://blog.csdn.net/qq_44390640/article/details/99817812
def mi_set_data(df, rat, tz=0):
    def nr_serv_cel(row):
        pos = row.serv_cel_pos
        if pos == 255:
            return 65535, -160, -50
        else:
            return row[f'PCI{pos}'], row[f'RSRP{pos}'], row[f'RSRQ{pos}']
    if rat == 'lte':
        df = df.rename(columns={
            'RSRP(dBm)': 'RSRP',
            'RSRQ(dB)': 'RSRQ',
            'Serving Cell Index': 'serv_cel_index',
            'Number of Neighbor Cells': 'num_neigh_cels',
            'Number of Detected Cells': 'num_cels',
            }).reindex(['Timestamp','type_id','PCI','RSRP','RSRQ','serv_cel_index','EARFCN','NR_ARFCN',
                        'num_cels','num_neigh_cels','serv_cel_pos','PCI0','RSRP0','RSRQ0',
                        *df.columns.to_list()[df.columns.get_loc('PCI1'):]], axis=1)
        df.loc[df['serv_cel_index'] == '(MI)Unknown', 'serv_cel_index'] = '3_SCell'
        df['num_cels'] = df['num_neigh_cels'] + 1
    if rat == 'nr':
        if df.empty:
            df = pd.DataFrame(columns=['Timestamp','type_id','PCI','RSRP','RSRQ','serv_cel_index','EARFCN','NR_ARFCN',
                                       'num_cels','num_neigh_cels','serv_cel_pos','PCI0','RSRP0','RSRQ0'])
        else:
            df = df.rename(columns={
                'Raster ARFCN': 'NR_ARFCN',
                'Serving Cell Index': 'serv_cel_pos',
                'Num Cells': 'num_cels',
                }).reindex(['Timestamp','type_id','PCI','RSRP','RSRQ','serv_cel_index','EARFCN','NR_ARFCN',
                            'num_cels','num_neigh_cels','serv_cel_pos','PCI0','RSRP0','RSRQ0',
                            *df.columns.to_list()[df.columns.get_loc('PCI1'):]], axis=1)
            df.loc[df['serv_cel_pos'] != 255, 'serv_cel_index'] = 'PSCell'
            df[['PCI','RSRP','RSRQ']] = df.apply(nr_serv_cel, axis=1, result_type='expand')
            df.loc[df['serv_cel_pos'] == 255, 'num_neigh_cels'] = df['num_cels']
            df.loc[df['serv_cel_pos'] != 255, 'num_neigh_cels'] = df['num_cels'] - 1
    ### set dtypes
    df['Timestamp'] = pd.to_datetime(df['Timestamp']) + pd.Timedelta(hours=tz)
    df['type_id'] = df['type_id'].astype('category')
    df['serv_cel_index'] = df['serv_cel_index'].astype('category')
    df['EARFCN'] = df['EARFCN'].astype('Int32')
    df['NR_ARFCN'] = df['NR_ARFCN'].astype('Int32')
    df['num_cels'] = df['num_cels'].astype('UInt8')
    df['num_neigh_cels'] = df['num_neigh_cels'].astype('UInt8')
    df['serv_cel_pos'] = df['serv_cel_pos'].astype('UInt8')
    for tag in df.columns:
        if tag.startswith('PCI'):
            df[tag] = df[tag].astype('Int32')
        if tag.startswith(('RSRP','RSRQ')):
            df[tag] = df[tag].astype('float32')
    return df

## Uplink

In [56]:
if first_time:
    i = -1
    dfs_ul = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            if i in [16,17,18,19]:
                dfs_ul.append([pd.DataFrame()]*len(devices))
                continue
            dfs_ul.append([])
            st, et = [], []
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                data = os.path.join(datadir, date, exp, dev, trace, 'data', 'udp_uplk_loss_latency.csv')
                print(data, os.path.isfile(data))
                # print(i, j)
                df = pd.read_csv(data)
                df = set_data(df)
                dfs_ul[i].append(df.copy())
                st.append(df['seq'].array[0])
                et.append(df['seq'].array[-1])
            st, et = max(st), min(et)
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                dfs_ul[i][j] = dfs_ul[i][j][(dfs_ul[i][j]['seq'] >= st) & (dfs_ul[i][j]['seq'] <= et)].reset_index(drop=True)
    print(len(dfs_ul))

## Downlink

In [57]:
if first_time:
    i = -1
    dfs_dl = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            if i in [0,1,2,3]:
                dfs_dl.append([pd.DataFrame()]*len(devices))
                continue
            dfs_dl.append([])
            st, et = [], []
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                data = os.path.join(datadir, date, exp, dev, trace, 'data', 'udp_dnlk_loss_latency.csv')
                print(data, os.path.isfile(data))
                # print(i, j)
                df = pd.read_csv(data)
                df = set_data(df)
                dfs_dl[i].append(df.copy())
                st.append(df['seq'].array[0])
                et.append(df['seq'].array[-1])
            st, et = max(st), min(et)
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                dfs_dl[i][j] = dfs_dl[i][j][(dfs_dl[i][j]['seq'] >= st) & (dfs_dl[i][j]['seq'] <= et)].reset_index(drop=True)
    print(len(dfs_dl))

## Handover

In [58]:
if first_time:
    i = -1
    dfs_ho = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfs_ho.append([])
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                path = os.path.join(datadir, date, exp, dev, trace, 'data')
                data = os.path.join(path, [s for s in os.listdir(path) if s.startswith('diag_log_') and s.endswith('_rrc.csv')][0])
                print(data, os.path.isfile(data))
                # print(i, j)
                df = pd.read_csv(data)
                df, _, _ = mi_parse_ho(df, tz=8)
                dfs_ho[i].append(df.copy())
    print(len(dfs_ho))

## LTE Cell

In [59]:
if first_time:
    i = -1
    dfs_lte = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfs_lte.append([])
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                path = os.path.join(datadir, date, exp, dev, trace, 'data')
                data = os.path.join(path, [s for s in os.listdir(path) if s.startswith('diag_log_') and s.endswith('_ml1.csv') and not s.endswith('_nr_ml1.csv')][0])
                print(data, os.path.isfile(data))
                # print(i, j)
                df = pd.read_csv(data)
                df = mi_set_data(df, 'lte', tz=8)
                dfs_lte[i].append(df.copy())
    print(len(dfs_lte))

## NR Cell

In [60]:
if first_time:
    i = -1
    dfs_nr = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfs_nr.append([])
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                path = os.path.join(datadir, date, exp, dev, trace, 'data')
                data = os.path.join(path, [s for s in os.listdir(path) if s.startswith('diag_log_') and s.endswith('_nr_ml1.csv')][0])
                print(data, os.path.isfile(data))
                # print(i, j)
                df = pd.read_csv(data)
                df = mi_set_data(df, 'nr', tz=8)
                dfs_nr[i].append(df.copy())
    print(len(dfs_nr))

In [61]:
if first_time:
    df = dfs_ul[0][0].copy()

    plr = round(df.lost.mean() * 100, 4)
    elr = round(df[~df.lost].excl.mean() * 100, 4)
    plelr = round(df.excl.mean() * 100, 4)
    avg_l = round(df[~df.lost].latency.mean(), 6)
    min_l = round(df[~df.lost].latency.min(), 6)
    max_l = round(df[~df.lost].latency.max(), 6)
    mdn_l = round(df[~df.lost].latency.median(), 6)
    var_l = round(df[~df.lost].latency.var(), 6)
    std_l = round(df[~df.lost].latency.std(), 6)
    jitter = round(df.loc[~df.lost, 'latency'].diff().abs().mean(), 6)

    print('packet loss rate (%):      ', plr)
    print('excessive latency rate (%):', elr)
    print('plr + elr (%):             ', plelr)
    print('average latency:           ', avg_l)
    print('min latency:               ', min_l)
    print('max latency:               ', max_l)
    print('median latency:            ', mdn_l)
    print('latency variance:          ', var_l)
    print('latency standard deviation:', std_l)
    print('latency jitter:            ', jitter)

    display(df)

# Single Radio Processing

In [62]:
sorter = ['stable',
          'LTE_HO','MN_HO','SN_HO','MNSN_HO','SN_Rel','SN_Setup','SN_Rel_MN_HO','SN_Setup_MN_HO',
          'SCG_Failure_t310-Expiry (0)','SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)','SCG_Failure_synchReconfigFailureSCG (3)',
          'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
          'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
          'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
# mcg failure types: https://www.sharetechnote.com/html/Handbook_LTE_RRC_ConnectionReestablishment.html (0)(1)(2)
# scg failure types: https://www.sharetechnote.com/html/5G/5G_Release17.html (1)(3)

print(len(sorter))
print(sorter)

22
['stable', 'LTE_HO', 'MN_HO', 'SN_HO', 'MNSN_HO', 'SN_Rel', 'SN_Setup', 'SN_Rel_MN_HO', 'SN_Setup_MN_HO', 'SCG_Failure_t310-Expiry (0)', 'SCG_Failure_randomAccessProblem (1)', 'SCG_Failure_rlc-MaxNumRetx (2)', 'SCG_Failure_synchReconfigFailureSCG (3)', 'SCG_Failure_scg-ReconfigFailure (4)', 'SCG_Failure_srb3-IntegrityFailure (5)', 'SCG_Failure_other-r16 (6)', 'MCG_Failure_reconfigurationFailure (0)', 'MCG_Failure_handoverFailure (1)', 'MCG_Failure_otherFailure (2)', 'NAS_Recovery_reconfigurationFailure (0)', 'NAS_Recovery_handoverFailure (1)', 'NAS_Recovery_otherFailure (2)']


In [63]:
def sr_round_to_secound(df_ul, df_dl, df_lte, df_nr, df_ho):
    ### UL Stats
    if df_ul.empty:
        df_ul = pd.DataFrame(columns=['seq', 'rpkg', 'frame_id', 'Timestamp', 'Timestamp_epoch',
                                    'lost', 'excl', 'latency',
                                    'xmit_time', 'xmit_time_epoch', 'arr_time', 'arr_time_epoch'])
        df_ul['Timestamp'] = pd.to_datetime(df_ul['Timestamp'])
    df_ul['Timestamp'] = df_ul['Timestamp'].dt.round('S')
    dfr = df_ul[df_ul['lost'] == False].copy().reset_index(drop=True)
    dfr['diff'] = dfr['latency'].diff().abs()
    ts_group = df_ul.groupby(['Timestamp'])
    tsr_group = dfr.groupby(['Timestamp'])

    dfagg_ul = ts_group['lost'].agg(['count','sum','mean']).copy().reset_index()
    dfagg_ul = dfagg_ul.rename(columns={'count':'tx_count', 'sum':'lost', 'mean':'PLR'})
    dfagg_ul['PLR'] = dfagg_ul['PLR'] * 100

    dfagg_ul1 = tsr_group['excl'].agg(['count','sum','mean']).copy().reset_index()
    dfagg_ul1 = dfagg_ul1.rename(columns={'count':'rx_count', 'sum':'excl', 'mean':'ELR'})
    dfagg_ul1['ELR'] = dfagg_ul1['ELR'] * 100
    dfagg_ul = pd.merge(dfagg_ul, dfagg_ul1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ul1 = ts_group['excl'].agg(['mean']).copy().reset_index()
    dfagg_ul1 = dfagg_ul1.rename(columns={'mean':'PLELR'})
    dfagg_ul1['PLELR'] = dfagg_ul1['PLELR'] * 100
    dfagg_ul = pd.merge(dfagg_ul, dfagg_ul1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ul1 = tsr_group['latency'].agg(['mean','min','max','median','std','var']).copy().reset_index()
    dfagg_ul1 = dfagg_ul1.add_suffix('_L')
    dfagg_ul1 = dfagg_ul1.rename(columns={'Timestamp_L':'Timestamp', 'mean_L':'avg_L'})
    dfagg_ul = pd.merge(dfagg_ul, dfagg_ul1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ul1 = tsr_group['diff'].agg(['mean']).copy().reset_index()
    dfagg_ul1 = dfagg_ul1.rename(columns={'mean':'jitter_L'})
    dfagg_ul = pd.merge(dfagg_ul, dfagg_ul1, on='Timestamp', how='outer').copy().reset_index(drop=True)
    # jitter := average of a bunch of "absolute value of first-order difference"
    
    dfagg_ul['tx_count'] = dfagg_ul['tx_count'].astype('Int32')
    dfagg_ul['lost'] = dfagg_ul['lost'].astype('Int32')
    dfagg_ul['PLR'] = dfagg_ul['PLR'].astype('float32')
    dfagg_ul['rx_count'] = dfagg_ul['rx_count'].astype('Int32')
    dfagg_ul['excl'] = dfagg_ul['excl'].astype('Int32')
    dfagg_ul['ELR'] = dfagg_ul['ELR'].astype('float32')
    dfagg_ul['PLELR'] = dfagg_ul['PLELR'].astype('float32')
    dfagg_ul['avg_L'] = dfagg_ul['avg_L'].astype('float32')
    dfagg_ul['min_L'] = dfagg_ul['min_L'].astype('float32')
    dfagg_ul['max_L'] = dfagg_ul['max_L'].astype('float32')
    dfagg_ul['median_L'] = dfagg_ul['median_L'].astype('float32')
    dfagg_ul['std_L'] = dfagg_ul['std_L'].astype('float32')
    dfagg_ul['var_L'] = dfagg_ul['var_L'].astype('float64')
    dfagg_ul['jitter_L'] = dfagg_ul['jitter_L'].astype('float32')

    # display(dfagg_ul)

    ### DL Stats
    if df_dl.empty:
        df_dl = pd.DataFrame(columns=['seq', 'rpkg', 'frame_id', 'Timestamp', 'Timestamp_epoch',
                                    'lost', 'excl', 'latency',
                                    'xmit_time', 'xmit_time_epoch', 'arr_time', 'arr_time_epoch'])
        df_dl['Timestamp'] = pd.to_datetime(df_dl['Timestamp'])
    df_dl['Timestamp'] = df_dl['Timestamp'].dt.round('S')
    dfr = df_dl[df_dl['lost'] == False].copy().reset_index(drop=True)
    dfr['diff'] = dfr['latency'].diff().abs()
    ts_group = df_dl.groupby(['Timestamp'])
    tsr_group = dfr.groupby(['Timestamp'])

    dfagg_dl = ts_group['lost'].agg(['count','sum','mean']).copy().reset_index()
    dfagg_dl = dfagg_dl.rename(columns={'count':'tx_count', 'sum':'lost', 'mean':'PLR'})
    dfagg_dl['PLR'] = dfagg_dl['PLR'] * 100

    dfagg_dl1 = tsr_group['excl'].agg(['count','sum','mean']).copy().reset_index()
    dfagg_dl1 = dfagg_dl1.rename(columns={'count':'rx_count', 'sum':'excl', 'mean':'ELR'})
    dfagg_dl1['ELR'] = dfagg_dl1['ELR'] * 100
    dfagg_dl = pd.merge(dfagg_dl, dfagg_dl1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_dl1 = ts_group['excl'].agg(['mean']).copy().reset_index()
    dfagg_dl1 = dfagg_dl1.rename(columns={'mean':'PLELR'})
    dfagg_dl1['PLELR'] = dfagg_dl1['PLELR'] * 100
    dfagg_dl = pd.merge(dfagg_dl, dfagg_dl1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_dl1 = tsr_group['latency'].agg(['mean','min','max','median','std','var']).copy().reset_index()
    dfagg_dl1 = dfagg_dl1.add_suffix('_L')
    dfagg_dl1 = dfagg_dl1.rename(columns={'Timestamp_L':'Timestamp', 'mean_L':'avg_L'})
    dfagg_dl = pd.merge(dfagg_dl, dfagg_dl1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_dl1 = tsr_group['diff'].agg(['mean']).copy().reset_index()
    dfagg_dl1 = dfagg_dl1.rename(columns={'mean':'jitter_L'})
    dfagg_dl = pd.merge(dfagg_dl, dfagg_dl1, on='Timestamp', how='outer').copy().reset_index(drop=True)
    # jitter := average of a bunch of "absolute value of first-order difference"

    dfagg_dl['tx_count'] = dfagg_dl['tx_count'].astype('Int32')
    dfagg_dl['lost'] = dfagg_dl['lost'].astype('Int32')
    dfagg_dl['PLR'] = dfagg_dl['PLR'].astype('float32')
    dfagg_dl['rx_count'] = dfagg_dl['rx_count'].astype('Int32')
    dfagg_dl['excl'] = dfagg_dl['excl'].astype('Int32')
    dfagg_dl['ELR'] = dfagg_dl['ELR'].astype('float32')
    dfagg_dl['PLELR'] = dfagg_dl['PLELR'].astype('float32')
    dfagg_dl['avg_L'] = dfagg_dl['avg_L'].astype('float32')
    dfagg_dl['min_L'] = dfagg_dl['min_L'].astype('float32')
    dfagg_dl['max_L'] = dfagg_dl['max_L'].astype('float32')
    dfagg_dl['median_L'] = dfagg_dl['median_L'].astype('float32')
    dfagg_dl['std_L'] = dfagg_dl['std_L'].astype('float32')
    dfagg_dl['var_L'] = dfagg_dl['var_L'].astype('float64')
    dfagg_dl['jitter_L'] = dfagg_dl['jitter_L'].astype('float32')
    
    # display(dfagg_dl)

    ### LTE
    df_lte = df_lte[df_lte['serv_cel_index'] == 'PCell'].copy().reset_index(drop=True)
    df_lte['Timestamp'] = df_lte['Timestamp'].dt.round('S')
    tsl_group = df_lte.groupby(['Timestamp'])

    dfagg_lte = df_lte.loc[~df_lte.duplicated(subset=['Timestamp']), ['Timestamp','PCI','EARFCN']].copy().reset_index(drop=True)

    dfagg_lte1 = tsl_group['RSRP'].agg(['mean']).copy().reset_index()
    dfagg_lte1 =  dfagg_lte1.rename(columns={'mean':'RSRP'})
    dfagg_lte = pd.merge(dfagg_lte, dfagg_lte1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_lte1 = tsl_group['RSRQ'].agg(['mean']).copy().reset_index()
    dfagg_lte1 =  dfagg_lte1.rename(columns={'mean':'RSRQ'})
    dfagg_lte = pd.merge(dfagg_lte, dfagg_lte1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    # display(dfagg_lte)

    ### NR
    df_nr = df_nr[df_nr['serv_cel_index'] == 'PSCell'].copy().reset_index(drop=True)
    df_nr['Timestamp'] = df_nr['Timestamp'].dt.round('S')
    tsn_group = df_nr.groupby(['Timestamp'])

    dfagg_nr = df_nr.loc[~df_nr.duplicated(subset=['Timestamp']), ['Timestamp','PCI','NR_ARFCN']].copy().reset_index(drop=True)
    dfagg_nr = dfagg_nr.rename(columns={'PCI':'nrPCI', 'NR_ARFCN':'nrARFCN'})

    dfagg_nr1 = tsn_group['RSRP'].agg(['mean']).copy().reset_index()
    dfagg_nr1 =  dfagg_nr1.rename(columns={'mean':'nrRSRP'})
    dfagg_nr = pd.merge(dfagg_nr, dfagg_nr1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_nr1 = tsn_group['RSRQ'].agg(['mean']).copy().reset_index()
    dfagg_nr1 =  dfagg_nr1.rename(columns={'mean':'nrRSRQ'})
    dfagg_nr = pd.merge(dfagg_nr, dfagg_nr1, on='Timestamp', how='outer').copy().reset_index(drop=True)

    # display(dfagg_nr)

    ### Concat pkt, LTE, NR
    dfagg_cell = pd.merge(dfagg_lte, dfagg_nr, on='Timestamp', how='outer').copy().reset_index(drop=True)
    dfagg_ul = pd.merge(dfagg_ul, dfagg_cell, on='Timestamp', how='left').copy().reset_index(drop=True)

    for i, row in dfagg_ul[dfagg_ul['PCI'].isna()].iterrows():
        j = i - 1
        while j >= 0 and pd.isna(dfagg_ul.at[j, 'PCI']):
            j -= 1
        if i != 0:
            dfagg_ul.loc[i, ['PCI','EARFCN','RSRP','RSRQ']] = dfagg_ul.loc[j, ['PCI','EARFCN','RSRP','RSRQ']]
    
    if df_nr.empty:
        dfagg_ul['nrRSRP'] = -160
        dfagg_ul['nrRSRQ'] = -50

    # print(dfagg_ul['PCI'].isna().sum())
    # print(dfagg_ul['nrPCI'].isna().sum())
    # display(dfagg_ul)

    dfagg_dl = pd.merge(dfagg_dl, dfagg_cell, on='Timestamp', how='left').copy().reset_index(drop=True)

    for i, row in dfagg_dl[dfagg_dl['PCI'].isna()].iterrows():
        j = i - 1
        while j >= 0 and pd.isna(dfagg_dl.at[j, 'PCI']):
            j -= 1
        if i != 0:
            dfagg_dl.loc[i, ['PCI','EARFCN','RSRP','RSRQ']] = dfagg_dl.loc[j, ['PCI','EARFCN','RSRP','RSRQ']]
    
    if df_nr.empty:
        dfagg_dl['nrRSRP'] = -160
        dfagg_dl['nrRSRQ'] = -50

    # print(dfagg_dl['PCI'].isna().sum())
    # print(dfagg_dl['nrPCI'].isna().sum())
    # display(dfagg_dl)

    ### Handover
    ## ping-pong event
    # df_ho['mnpp'] = pd.Series(0, dtype='Int8')
    # df_ho['snpp'] = pd.Series(0, dtype='Int8')
    df_ho['mnpp'] = 0
    df_ho['snpp'] = 0
    df_ho['mnpp'] = df_ho['mnpp'].astype('Int16')
    df_ho['snpp'] = df_ho['snpp'].astype('Int16')
    qlte = myQueue(7)
    qnr = myQueue(7)
    for i, row in df_ho.iterrows():
        if row.ho_type == 'Conn_Rel':
            qlte.clear()
            qnr.clear()
            continue
        if row.ho_type in ['Conn_Setup','LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO']:
            if (row.tPCI, row.tFreq) in qlte.tolist()[:-1]:
                df_ho.at[i, 'mnpp'] = 1
            if (row.tPCI, row.tFreq) != qlte.rear():
                qlte.push((row.tPCI, row.tFreq))
        if row.ho_type in ['SN_Setup','SN_HO','MNSN_HO','SN_Rel','LTE_HO','SN_Rel_MN_HO','SN_Setup_MN_HO']:
            if row.ho_type in ['SN_Rel','LTE_HO','SN_Rel_MN_HO']:
                qnr.clear()
                continue
            if row.tnrPCI in qnr.tolist()[:-1]:
                df_ho.at[i, 'snpp'] = 1
            if row.tnrPCI != qnr.rear():
                qnr.push(row.tnrPCI)
    ## ho_type1, ho_type2
    df_ho['ho_type1'] = 'sn_change'
    df_ho['ho_type2'] = 'sn_change'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & (df_ho['sFreq'] == df_ho['tFreq']), 'ho_type1'] = 'intra_freq'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & (df_ho['sFreq'] != df_ho['tFreq']), 'ho_type1'] = 'inter_freq'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & (df_ho['sPCI'] == df_ho['tPCI']), 'ho_type2'] = 'intra_sector'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & (df_ho['sPCI'] != df_ho['tPCI']), 'ho_type2'] = 'inter_sector'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & df_ho['eNB'].notna() & df_ho['eNB1'].notna() & (df_ho['eNB'] != df_ho['eNB1']), 'ho_type2'] = 'inter_enb'
    df_ho.loc[(np.in1d(df_ho['ho_type'], ['LTE_HO','MN_HO','MNSN_HO','SN_Rel_MN_HO','SN_Setup_MN_HO'])) & df_ho['eNB'].isna() | df_ho['eNB1'].isna(), 'ho_type2'] = 'unknown_enb'
    ## rlf cause
    df_ho['ho_type'] = df_ho['ho_type'].astype('string')
    df_ho['cause'] = df_ho['cause'].astype('string')
    df_ho.loc[np.in1d(df_ho['ho_type'], ['SCG_Failure','MCG_Failure','NAS_Recovery']), 'ho_type'] = \
        df_ho.loc[np.in1d(df_ho['ho_type'], ['SCG_Failure','MCG_Failure','NAS_Recovery']), 'ho_type'] + '_' + df_ho.loc[(np.in1d(df_ho['ho_type'], ['SCG_Failure','MCG_Failure','NAS_Recovery'])), 'cause']
    ## define ho_type0/1/2
    df_ho = df_ho[~np.in1d(df_ho['ho_type'], ['Conn_Setup','Conn_Rel'])].copy().reset_index(drop=True)
    handover_type = ['stable',
                    'LTE_HO','MN_HO','SN_HO','MNSN_HO','SN_Rel','SN_Setup','SN_Rel_MN_HO','SN_Setup_MN_HO',
                    'SCG_Failure_t310-Expiry (0)','SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)','SCG_Failure_synchReconfigFailureSCG (3)',
                    'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                    'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                    'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
    handover_type1 = ['sn_change','intra_freq','inter_freq']
    handover_type2 = ['sn_change','intra_sector','inter_sector','inter_enb','unknown_enb']
    df_ho = pd.concat([pd.DataFrame(handover_type, columns=['ho_type']),
                    pd.DataFrame(handover_type1, columns=['ho_type1']),
                    pd.DataFrame(handover_type2, columns=['ho_type2']),
                    df_ho], ignore_index=True)
    df_ho = df_ho[['Timestamp','ho_type','ho_type1','ho_type2','st_scel','mnpp','snpp']]
    df_ho['ho_type'] = df_ho['ho_type'].astype('category')
    df_ho['ho_type1'] = df_ho['ho_type1'].astype('category')
    df_ho['ho_type2'] = df_ho['ho_type2'].astype('category')
    df_ho['ho_type'] = df_ho['ho_type'].cat.set_categories(handover_type)
    df_ho['ho_type1'] = df_ho['ho_type1'].cat.set_categories(handover_type1)
    df_ho['ho_type2'] = df_ho['ho_type2'].cat.set_categories(handover_type2)
    ## generate dummies
    dum0 = pd.get_dummies(df_ho.ho_type).astype('Int16')
    dum1 = pd.get_dummies(df_ho.ho_type1).astype('Int16')
    dum2 = pd.get_dummies(df_ho.ho_type2).astype('Int16')
    df_ho = pd.concat([df_ho, dum0, dum1, dum2], axis=1)
    df_ho = df_ho.dropna(subset='Timestamp').copy().reset_index(drop=True)
    ## count
    df_ho['Timestamp'] = df_ho['Timestamp'].dt.round('S')
    tsh_group = df_ho.groupby(['Timestamp'])

    dfagg_ho = df_ho.loc[~df_ho.duplicated(subset=['Timestamp']), ['Timestamp','ho_type','ho_type1','ho_type2']].copy().reset_index(drop=True)
    dfagg_ho1 = tsh_group['ho_type'].agg(['count']).copy().reset_index()
    dfagg_ho1 = dfagg_ho1.rename(columns={'count':'ho_num'})
    dfagg_ho = pd.merge(dfagg_ho, dfagg_ho1, on='Timestamp', how='outer')
    dfagg_ho['ho_num'] = dfagg_ho['ho_num'].astype('Int16')

    dfagg_ho = dfagg_ho.set_index('Timestamp')
    dfagg_ho['ho_type'] = dfagg_ho['ho_type'].astype('string')
    dfagg_ho['ho_type1'] = dfagg_ho['ho_type1'].astype('string')
    dfagg_ho['ho_type2'] = dfagg_ho['ho_type2'].astype('string')
    for i, row in df_ho[df_ho.duplicated(subset=['Timestamp'])].copy().iterrows():
        dfagg_ho.at[row.Timestamp, 'ho_type'] = dfagg_ho.at[row.Timestamp, 'ho_type'] + '&' + row.ho_type
        dfagg_ho.at[row.Timestamp, 'ho_type1'] = dfagg_ho.at[row.Timestamp, 'ho_type1'] + '&' + row.ho_type1
        dfagg_ho.at[row.Timestamp, 'ho_type2'] = dfagg_ho.at[row.Timestamp, 'ho_type2'] + '&' + row.ho_type2
        # dfagg_ho.at[row.Timestamp, 'ho_src'] = dfagg_ho.at[row.Timestamp, 'ho_src'] + '&' + row.ho_src
        # dfagg_ho.at[row.Timestamp, 'ho_tgt'] = dfagg_ho.at[row.Timestamp, 'ho_tgt'] + '&' + row.ho_tgt
    dfagg_ho = dfagg_ho.reset_index()

    dfagg_ho = pd.merge(dfagg_ho, tsh_group['st_scel'].max().copy().reset_index(),
                        on='Timestamp', how='outer')
    dfagg_ho = pd.merge(dfagg_ho, tsh_group[['mnpp', 'snpp']].sum().copy().reset_index(),
                        on='Timestamp', how='outer')
    dfagg_ho = pd.merge(dfagg_ho, tsh_group[[*handover_type, *handover_type1, *handover_type2]].sum().copy().reset_index(),
                        on='Timestamp', how='outer')
    ## deal with duplicate columns
    dfagg_ho = dfagg_ho.loc[:, ~dfagg_ho.columns.duplicated()].copy()
    
    # display(dfagg_ho)

    ### Concat pkt, Handover
    dfagg_ul = pd.merge(dfagg_ul, dfagg_ho, on='Timestamp', how='left').copy().reset_index(drop=True)
    for tag in ['ho_num','st_scel','mnpp','snpp',*handover_type,*handover_type1,*handover_type2]:
        dfagg_ul[tag] = dfagg_ul[tag].fillna(0)
        
    dfagg_dl = pd.merge(dfagg_dl, dfagg_ho, on='Timestamp', how='left').copy().reset_index(drop=True)
    for tag in ['ho_num','st_scel','mnpp','snpp',*handover_type,*handover_type1,*handover_type2]:
        dfagg_dl[tag] = dfagg_dl[tag].fillna(0)
        
    ### add stable state
    dfagg_ul.loc[dfagg_ul['ho_type'].isna(), 'stable'] = 1
    dfagg_ul['ho_type'] = dfagg_ul['ho_type'].fillna('stable')
    dfagg_ul['ho_type1'] = dfagg_ul['ho_type1'].fillna('stable')
    dfagg_ul['ho_type2'] = dfagg_ul['ho_type2'].fillna('stable')
    
    dfagg_dl.loc[dfagg_dl['ho_type'].isna(), 'stable'] = 1
    dfagg_dl['ho_type'] = dfagg_dl['ho_type'].fillna('stable')
    dfagg_dl['ho_type1'] = dfagg_dl['ho_type1'].fillna('stable')
    dfagg_dl['ho_type2'] = dfagg_dl['ho_type2'].fillna('stable')
    
    return dfagg_ul, dfagg_dl

In [64]:
if first_time:
    i = -1
    dfaggs_ul_sr = []
    dfaggs_dl_sr = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfaggs_ul_sr.append([])
            dfaggs_dl_sr.append([])
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                path = os.path.join(datadir, date, exp, 'combo', trace)
                makedir(path)
                # print(i, j)
                
                dfagg_ul, dfagg_dl = sr_round_to_secound(dfs_ul[i][j].copy(), dfs_dl[i][j].copy(), dfs_lte[i][j].copy(), dfs_nr[i][j].copy(), dfs_ho[i][j].copy())
                # dfagg_ul = dfagg_ul.head(-1).tail(-1).reset_index(drop=True)
                # dfagg_dl = dfagg_dl.head(-1).tail(-1).reset_index(drop=True)
                print(os.path.join(path, f'udp_uplk_integrate_sec_{schm}.pkl'))
                dfagg_ul.to_pickle(os.path.join(path, f'udp_uplk_integrate_sec_{schm}.pkl'))
                print(os.path.join(path, f'udp_dnlk_integrate_sec_{schm}.pkl'))
                dfagg_dl.to_pickle(os.path.join(path, f'udp_dnlk_integrate_sec_{schm}.pkl'))
                
                dfaggs_ul_sr[i].append(dfagg_ul)
                dfaggs_dl_sr[i].append(dfagg_dl)
    print(len(dfaggs_ul_sr))
    print(len(dfaggs_dl_sr))

In [65]:
if not first_time:
    i = -1
    dfaggs_ul_sr = []
    dfaggs_dl_sr = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfaggs_ul_sr.append([])
            dfaggs_dl_sr.append([])
            for j, (dev, schm) in enumerate(zip(devices, schemes)):
                path = os.path.join(datadir, date, exp, 'combo', trace)
                data1 = os.path.join(path, f'udp_uplk_integrate_sec_{schm}.pkl')
                data2 = os.path.join(path, f'udp_dnlk_integrate_sec_{schm}.pkl')
                print(data1, os.path.isfile(data1))
                print(data2, os.path.isfile(data2))
                # print(i, j)
                dfagg_ul = pd.read_pickle(data1)
                dfagg_dl = pd.read_pickle(data2)
                # dfagg_ul = dfagg_ul.head(-1).tail(-1).reset_index(drop=True)
                # dfagg_dl = dfagg_dl.head(-1).tail(-1).reset_index(drop=True)
                dfaggs_ul_sr[i].append(dfagg_ul)
                dfaggs_dl_sr[i].append(dfagg_dl)
    print(len(dfaggs_ul_sr))
    print(len(dfaggs_dl_sr))

/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B1.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B1.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B7.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B7.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#03/udp_uplk_integrate_sec_B1.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM50

# Dual Radio Processing

In [66]:
# sorter1 = list(it.permutations(sorter, 2))
sorter1 = list(it.product(sorter, repeat=2))
sorter1 = ['+'.join([s[0],s[1]]) for s in sorter1]
print(len(sorter1))
print(sorter1)
sorter2 = [s.split('+')[0] for s in sorter1]
sorter3 = [s.split('+')[1] for s in sorter1]

484
['stable+stable', 'stable+LTE_HO', 'stable+MN_HO', 'stable+SN_HO', 'stable+MNSN_HO', 'stable+SN_Rel', 'stable+SN_Setup', 'stable+SN_Rel_MN_HO', 'stable+SN_Setup_MN_HO', 'stable+SCG_Failure_t310-Expiry (0)', 'stable+SCG_Failure_randomAccessProblem (1)', 'stable+SCG_Failure_rlc-MaxNumRetx (2)', 'stable+SCG_Failure_synchReconfigFailureSCG (3)', 'stable+SCG_Failure_scg-ReconfigFailure (4)', 'stable+SCG_Failure_srb3-IntegrityFailure (5)', 'stable+SCG_Failure_other-r16 (6)', 'stable+MCG_Failure_reconfigurationFailure (0)', 'stable+MCG_Failure_handoverFailure (1)', 'stable+MCG_Failure_otherFailure (2)', 'stable+NAS_Recovery_reconfigurationFailure (0)', 'stable+NAS_Recovery_handoverFailure (1)', 'stable+NAS_Recovery_otherFailure (2)', 'LTE_HO+stable', 'LTE_HO+LTE_HO', 'LTE_HO+MN_HO', 'LTE_HO+SN_HO', 'LTE_HO+MNSN_HO', 'LTE_HO+SN_Rel', 'LTE_HO+SN_Setup', 'LTE_HO+SN_Rel_MN_HO', 'LTE_HO+SN_Setup_MN_HO', 'LTE_HO+SCG_Failure_t310-Expiry (0)', 'LTE_HO+SCG_Failure_randomAccessProblem (1)', 'LTE_HO

In [67]:
def dr_round_to_secound(dfagg1, dfagg2, df1, df2):
    if df1.empty:
        df1 = pd.DataFrame(columns=['seq', 'rpkg', 'frame_id', 'Timestamp', 'Timestamp_epoch',
                                    'lost', 'excl', 'latency',
                                    'xmit_time', 'xmit_time_epoch', 'arr_time', 'arr_time_epoch'])
        df1['Timestamp'] = pd.to_datetime(df1['Timestamp'])
    if df2.empty:
        df2 = pd.DataFrame(columns=['seq', 'rpkg', 'frame_id', 'Timestamp', 'Timestamp_epoch',
                                    'lost', 'excl', 'latency',
                                    'xmit_time', 'xmit_time_epoch', 'arr_time', 'arr_time_epoch'])
        df2['Timestamp'] = pd.to_datetime(df2['Timestamp'])
    
    df = df1.merge(df2, on=['seq','Timestamp','Timestamp_epoch'], suffixes=('_m','_s'))
    df['Timestamp'] = df['Timestamp'].dt.round('S')
    df['lost_ms'] = df['lost_m'] & df['lost_s']
    df['lost_mlss'] = df['lost_m'] & ~df['lost_s']
    df['excl_ms'] = df['excl_m'] & df['excl_s']
    df['excl_mess'] = df['excl_m'] & ~df['excl_s']
    df['latency_ms'] = df[['latency_m','latency_s']].min(axis=1)

    dfr = df[df['lost_ms'] == False].copy().reset_index(drop=True)
    dfr['diff_ms'] = dfr['latency_ms'].diff().abs()
    ts_group = df.groupby(['Timestamp'])
    tsr_group = dfr.groupby(['Timestamp'])

    dfagg = ts_group['lost_ms'].agg(['count','sum','mean']).copy().reset_index()
    dfagg = dfagg.rename(columns={'count':'tx_count', 'sum':'lost_ms', 'mean':'PLR_ms'})
    dfagg['PLR_ms'] = dfagg['PLR_ms'] * 100

    dfagg_ = ts_group['lost_mlss'].agg(['sum','mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'sum':'lost_mlss', 'mean':'PLR_mlss'})
    dfagg_['PLR_mlss'] = dfagg_['PLR_mlss'] * 100
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    ## Note. lost_mlss 可能會轉化成 excl_ms 或 excl_mess
    dfagg_ = tsr_group['excl_ms'].agg(['count','sum','mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'count':'rx_count', 'sum':'excl_ms', 'mean':'ELR_ms'})
    dfagg_['ELR_ms'] = dfagg_['ELR_ms'] * 100
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ = ts_group['excl_ms'].agg(['mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'mean':'PLELR_ms'})
    dfagg_['PLELR_ms'] = dfagg_['PLELR_ms'] * 100
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ = tsr_group['excl_mess'].agg(['sum','mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'sum':'excl_mess', 'mean':'ELR_mess'})
    dfagg_['ELR_mess'] = dfagg_['ELR_mess'] * 100
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ = ts_group['excl_mess'].agg(['mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'mean':'PLELR_mless'})
    dfagg_['PLELR_mless'] = dfagg_['PLELR_mless'] * 100
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ = tsr_group['latency_ms'].agg(['mean','min','max','median','std','var']).copy().reset_index()
    dfagg_ = dfagg_.add_suffix('_L')
    dfagg_ = dfagg_.rename(columns={'Timestamp_L':'Timestamp', 'mean_L':'avg_L'})
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)

    dfagg_ = tsr_group['diff_ms'].agg(['mean']).copy().reset_index()
    dfagg_ = dfagg_.rename(columns={'mean':'jitter_L'})
    dfagg = pd.merge(dfagg, dfagg_, on='Timestamp', how='outer').copy().reset_index(drop=True)
    # jitter := average of a bunch of "absolute value of first-order difference"
    dfagg['tx_count'] = dfagg['tx_count'].astype('Int32')
    dfagg['lost_ms'] = dfagg['lost_ms'].astype('Int32')
    dfagg['PLR_ms'] = dfagg['PLR_ms'].astype('float32')
    dfagg['lost_mlss'] = dfagg['lost_mlss'].astype('Int32')
    dfagg['PLR_mlss'] = dfagg['PLR_mlss'].astype('float32')
    dfagg['rx_count'] = dfagg['rx_count'].astype('Int32')
    dfagg['excl_ms'] = dfagg['excl_ms'].astype('Int32')
    dfagg['ELR_ms'] = dfagg['ELR_ms'].astype('float32')
    dfagg['PLELR_ms'] = dfagg['PLELR_ms'].astype('float32')
    dfagg['excl_mess'] = dfagg['excl_mess'].astype('Int32')
    dfagg['ELR_mess'] = dfagg['ELR_mess'].astype('float32')
    dfagg['PLELR_mless'] = dfagg['PLELR_mless'].astype('float32')
    dfagg['avg_L'] = dfagg['avg_L'].astype('float32')
    dfagg['min_L'] = dfagg['min_L'].astype('float32')
    dfagg['max_L'] = dfagg['max_L'].astype('float32')
    dfagg['median_L'] = dfagg['median_L'].astype('float32')
    dfagg['std_L'] = dfagg['std_L'].astype('float32')
    dfagg['var_L'] = dfagg['var_L'].astype('float64')
    dfagg['jitter_L'] = dfagg['jitter_L'].astype('float32')

    dfagg = dfagg.merge(dfagg1[['Timestamp','PCI','EARFCN','RSRP','RSRQ','nrPCI','nrARFCN','nrRSRP','nrRSRQ']], on=['Timestamp'])
    dfagg = dfagg.merge(dfagg2[['Timestamp','PCI','EARFCN','RSRP','RSRQ','nrPCI','nrARFCN','nrRSRP','nrRSRQ']], on=['Timestamp'], suffixes=('_m','_s'))
    dfagg['RSRP_ms'] = dfagg[['RSRP_m','RSRP_s']].max(axis=1)
    dfagg['RSRQ_ms'] = dfagg[['RSRQ_m','RSRQ_s']].max(axis=1)
    dfagg['nrRSRP_ms'] = dfagg[['nrRSRP_m','nrRSRP_s']].max(axis=1)
    dfagg['nrRSRQ_ms'] = dfagg[['nrRSRQ_m','nrRSRQ_s']].max(axis=1)

    for tag in ['ho_type','ho_type1','ho_type2']:
        dfagg[tag] = dfagg1[tag] + '+' + dfagg2[tag]
        
    dfagg = dfagg.merge(dfagg1[['Timestamp','ho_num']], on=['Timestamp'])
    dfagg = dfagg.merge(dfagg2[['Timestamp','ho_num']], on=['Timestamp'], suffixes=('_m','_s'))
    dfagg['ho_num_ms'] = dfagg['ho_num_m'] + dfagg['ho_num_s']

    for tag in ['st_scel','mnpp','snpp']:
        dfagg = dfagg.merge(dfagg1[['Timestamp', tag]], on=['Timestamp'])
        dfagg = dfagg.merge(dfagg2[['Timestamp', tag]], on=['Timestamp'], suffixes=('_m','_s'))
        
    handover_type = ['stable',
                        'LTE_HO','MN_HO','SN_HO','MNSN_HO','SN_Rel','SN_Setup','SN_Rel_MN_HO','SN_Setup_MN_HO',
                        'SCG_Failure_t310-Expiry (0)','SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)','SCG_Failure_synchReconfigFailureSCG (3)',
                        'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                        'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                        'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
    handover_type1 = ['stable','sn_change','intra_freq','inter_freq']
    handover_type2 = ['stable','sn_change','intra_sector','inter_sector','inter_enb','unknown_enb']

    handover_type = list(it.product(handover_type, repeat=2))
    handover_type = ['+'.join([s[0],s[1]]) for s in handover_type]
    handover_type1 = list(it.product(handover_type1, repeat=2))
    handover_type1 = ['+'.join([s[0],s[1]]) for s in handover_type1]
    handover_type2 = list(it.product(handover_type2, repeat=2))
    handover_type2 = ['+'.join([s[0],s[1]]) for s in handover_type2]

    for item in handover_type:
        s1, s2 = item.split('+')
        dfagg[item] = dfagg1[s1] * dfagg2[s2]
    for item in handover_type1:
        s1, s2 = item.split('+')
        dfagg[item] = dfagg1[s1] * dfagg2[s2]
    for item in handover_type2:
        s1, s2 = item.split('+')
        dfagg[item] = dfagg1[s1] * dfagg2[s2]
    
    return dfagg

In [68]:
xs = list(it.permutations(range(len(schemes)), 2))
print(xs)

[(0, 1), (0, 2), (1, 0), (1, 2), (2, 0), (2, 1)]


In [69]:
if first_time:
    i = -1
    dfaggs_ul_dr = []
    dfaggs_dl_dr = []
    for date, traces in dates.items():
        for trace in traces:
            i += 1
            dfaggs_ul_dr.append([])
            dfaggs_dl_dr.append([])
            for x in xs:
                path = os.path.join(datadir, date, exp, 'combo', trace)
                makedir(path)
                # print(i, j)
                
                schm1 = schemes[x[0]]
                schm2 = schemes[x[1]]
                
                dfagg_ul = dr_round_to_secound(dfaggs_ul_sr[i][x[0]].copy(), dfaggs_ul_sr[i][x[1]].copy(), dfs_ul[i][x[0]].copy(), dfs_ul[i][x[1]].copy())
                dfagg_dl = dr_round_to_secound(dfaggs_dl_sr[i][x[0]].copy(), dfaggs_dl_sr[i][x[1]].copy(), dfs_dl[i][x[0]].copy(), dfs_dl[i][x[1]].copy())
                # dfagg_ul = dfagg_ul.head(-1).tail(-1).reset_index(drop=True)
                # dfagg_dl = dfagg_dl.head(-1).tail(-1).reset_index(drop=True)
                
                print(os.path.join(path, f'udp_uplk_integrate_sec_{schm1}_{schm2}.pkl'))
                dfagg_ul.to_pickle(os.path.join(path, f'udp_uplk_integrate_sec_{schm1}_{schm2}.pkl'))
                print(os.path.join(path, f'udp_dnlk_integrate_sec_{schm1}_{schm2}.pkl'))
                dfagg_dl.to_pickle(os.path.join(path, f'udp_dnlk_integrate_sec_{schm1}_{schm2}.pkl'))
                dfaggs_ul_dr[i].append(dfagg_ul)
                dfaggs_dl_dr[i].append(dfagg_dl)
    print(len(dfaggs_ul_dr))
    print(len(dfaggs_dl_dr))

In [70]:
xs = list(it.combinations(range(len(schemes)), 2))
print(xs)

[(0, 1), (0, 2), (1, 2)]


In [71]:
i = -1
dfaggs_ul_dr = []
dfaggs_dl_dr = []
for date, traces in dates.items():
    for trace in traces:
        i += 1
        dfaggs_ul_dr.append([])
        dfaggs_dl_dr.append([])
        for x in xs:
            path = os.path.join(datadir, date, exp, 'combo', trace)
            schm1 = schemes[x[0]]
            schm2 = schemes[x[1]]
            
            data1 = os.path.join(path, f'udp_uplk_integrate_sec_{schm1}_{schm2}.pkl')
            data2 = os.path.join(path, f'udp_dnlk_integrate_sec_{schm1}_{schm2}.pkl')
            print(data1, os.path.isfile(data1))
            print(data2, os.path.isfile(data2))
            # print(i, j)
            
            dfagg_ul = pd.read_pickle(data1)
            dfagg_dl = pd.read_pickle(data2)
            # dfagg_ul = dfagg_ul.head(-1).tail(-1).reset_index(drop=True)
            # dfagg_dl = dfagg_dl.head(-1).tail(-1).reset_index(drop=True)
            dfaggs_ul_dr[i].append(dfagg_ul)
            dfaggs_dl_dr[i].append(dfagg_dl)
print(len(dfaggs_ul_dr))
print(len(dfaggs_dl_dr))

/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B1_B7.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B1_B7.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B1_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B1_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_uplk_integrate_sec_B7_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#02/udp_dnlk_integrate_sec_B7_B8.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock_Udp_B1_B3_B7_B8_RM500Q/combo/#03/udp_uplk_integrate_sec_B1_B7.pkl True
/Users/jackbedford/Desktop/MOXA/Code/data/2023-03-15/_Bandlock

# One-Trip Analysis

In [72]:
print(schemes)
xs = list(it.combinations(range(len(schemes)), 2))
xs = [schemes[x[0]]+'+'+schemes[x[1]] for x in xs]
print(xs)

['B1', 'B7', 'B8']
['B1+B7', 'B1+B8', 'B7+B8']


## Single Radio

In [73]:
def get_sr_stats(df, BID):
    if df.empty:
        return pd.DataFrame()
    df = df.head(-1).tail(-1).reset_index(drop=True)
    df = df.drop(columns=['PCI','EARFCN','nrPCI','nrARFCN','ho_type','ho_type1','ho_type2'])
    df_stats = pd.DataFrame()
    df_stats.at[0, 'start'] = df.iloc[0]['Timestamp']
    df_stats.at[0, 'end'] = df.iloc[-1]['Timestamp']
    df_stats.at[0, 'time'] = len(df)
    df_stats.at[0, 'BID'] = BID

    df_stats = pd.concat([df_stats, df[['tx_count', 'lost', 'PLR', 'rx_count', 'excl', 'ELR', 'PLELR',
                                        'avg_L', 'min_L', 'max_L', 'median_L', 'std_L', 'var_L', 'jitter_L']].mean().to_frame().T], axis=1)
    df_stats['tx_count'] = df['tx_count'].sum()
    df_stats['lost'] = df['lost'].sum()
    df_stats['rx_count'] = df['rx_count'].sum()
    df_stats['excl'] = df['excl'].sum()
    df_stats['PLR'] = df_stats['lost'] / df_stats['tx_count'] * 100
    df_stats['ELR'] = df_stats['excl'] / df_stats['rx_count'] * 100
    df_stats['PLELR'] = (df_stats['lost'] + df_stats['excl']) / df_stats['tx_count'] * 100

    df_stats.at[0, 'RSRP'] = df['RSRP'].mean()
    df_stats.at[0, 'jitter_RSRP'] = df['RSRP'].diff().abs().mean()
    df_stats.at[0, 'RSRQ'] = df['RSRQ'].mean()
    df_stats.at[0, 'jitter_RSRQ'] = df['RSRQ'].diff().abs().mean()
    df_stats.at[0, 'nrRSRP'] = df['nrRSRP'].mean()
    df_stats.at[0, 'jitter_nrRSRP'] = df['nrRSRP'].diff().abs().mean()
    df_stats.at[0, 'nrRSRQ'] = df['nrRSRQ'].mean()
    df_stats.at[0, 'jitter_nrRSRQ'] = df['nrRSRQ'].diff().abs().mean()

    df_stats = pd.concat([df_stats, df.drop(columns=['Timestamp', 'tx_count', 'lost', 'PLR', 'rx_count', 'excl', 'ELR', 'PLELR',
                                                    'avg_L', 'min_L', 'max_L', 'median_L', 'std_L', 'var_L', 'jitter_L',
                                                    'RSRP', 'RSRQ', 'nrRSRP', 'nrRSRQ']).sum().to_frame().T], axis=1)
    df_stats.at[0, 'st_scel'] = df.loc[df['st_scel'] != 0, 'st_scel'].mean()
    
    return df_stats

In [74]:
N = len(dfaggs_ul_sr)
table_ul_sr = pd.DataFrame()

for i in range(N):
    for j, (dev, schm) in enumerate(zip(devices, schemes)):
        df = dfaggs_ul_sr[i][j]
        table_ul_sr = pd.concat([table_ul_sr, get_sr_stats(df, schm)])
table_ul_sr = table_ul_sr.sort_values(by=['start', 'BID']).reset_index(drop=True)
display(table_ul_sr)
table_ul_sr.to_pickle('table_ul_sr_stats.pkl')

start                 end   time BID  tx_count  lost  \
0  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B1    137493   151   
1  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B7    137493   235   
2  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B8    137493   475   
3  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B1    138993     8   
4  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B7    138993   210   
5  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B8    138993    29   
6  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B1    132994    18   
7  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B7    132994    40   
8  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B8    132994    58   
9  2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B1    136993     6   
10 2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B7    136993    52   
11 2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B8    136993   124   
12 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B1    140493    12   
13 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B7    140493    46   
14 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B8    140493    36   
15 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1    137494     8   
16 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B7    137494   317   
17 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B8    137494    30   
18 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1    143494     6   
19 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B7    143494    50   
20 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B8    143494    27   
21 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1    135494     5   
22 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B7    135494   176   
23 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B8    135494    30   
24 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1    138493     6   
25 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B7    138493   122   
26 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B8    138493    52   
27 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1    136493     8   
28 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B7    136493    43   
29 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B8    136493    31   
30 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1    133494     5   
31 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B7    133494    52   
32 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B8    133494   964   
33 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1    134994     5   
34 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B7    134994   894   
35 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B8    134994    31   
36 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B1    140494     4   
37 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B7    140494   119   
38 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B8    140494    27   
39 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1    136493     6   
40 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B7    136493   476   
41 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B8    136493    75   
42 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1    135493     3   
43 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B7    135493   113   
44 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B8    135493    64   
45 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1    133994     5   
46 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B7    133994   662   
47 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B8    133994   530   

         PLR  rx_count  excl       ELR     PLELR     avg_L     min_L  \
0   0.109824    137342     1  0.000728  0.110551  0.015277  0.010537   
1   0.170918    137258  2621  1.909543  2.077197  0.013228  0.006179   
2   0.345472    137018  6011  4.387015  4.717331  0.022657  0.011551   
3   0.005756    138985     5  0.003598  0.009353  0.018236  0.013375   
4   0.151087    138783  1155  0.832234  0.982064  0.012535  0.005774   
5   0.0

In [75]:
N = len(dfaggs_dl_sr)
table_dl_sr = pd.DataFrame()

for i in range(N):
    for j, (dev, schm) in enumerate(zip(devices, schemes)):
        df = dfaggs_dl_sr[i][j]
        table_dl_sr = pd.concat([table_dl_sr, get_sr_stats(df, schm)])
table_dl_sr = table_dl_sr.sort_values(by=['start', 'BID']).reset_index(drop=True)
display(table_dl_sr)
table_dl_sr.to_pickle('table_dl_sr_stats.pkl')

start                 end   time BID  tx_count  lost  \
0  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B1    139993    32   
1  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B7    139993   217   
2  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B8    139993  1326   
3  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1    137494     0   
4  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B7    137494  3045   
5  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B8    137494   262   
6  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1    143494     0   
7  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B7    143494  1500   
8  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B8    143494   149   
9  2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1    135494     0   
10 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B7    135494  1637   
11 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B8    135494   473   
12 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1    138494     0   
13 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B7    138494  2385   
14 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B8    138494  1448   
15 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1    136494     0   
16 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B7    136494  1742   
17 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B8    136494  1232   
18 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1    133494     0   
19 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B7    133494   876   
20 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B8    133494  2286   
21 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1    134994   688   
22 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B7    134994  2689   
23 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B8    134994   379   
24 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B1    139993   908   
25 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B7    139993  1518   
26 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B8    139993   143   
27 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1    136494  1316   
28 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B7    136494  3127   
29 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B8    136494     4   
30 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1    135494     0   
31 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B7    135494  3636   
32 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B8    135494   126   
33 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1    133994   702   
34 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B7    133994  2218   
35 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B8    133994  2492   
36 2023-03-16 20:59:06 2023-03-16 21:03:37  270.0  B1    134479     0   
37 2023-03-16 20:59:06 2023-03-16 21:03:37  272.0  B7    135584     0   
38 2023-03-16 20:59:06 2023-03-16 21:03:37  272.0  B8    135839     0   
39 2023-03-16 21:09:56 2023-03-16 21:14:27  272.0  B1    135993     0   
40 2023-03-16 21:09:56 2023-03-16 21:14:27  271.0  B7    134860     0   
41 2023-03-16 21:09:56 2023-03-16 21:14:27  272.0  B8    135351     0   
42 2023-03-16 21:20:53 2023-03-16 21:25:17  265.0  B1    132494     0   
43 2023-03-16 21:20:53 2023-03-16 21:25:17  264.0  B7    131084     0   
44 2023-03-16 21:20:53 2023-03-16 21:25:17  264.0  B8    131590     0   
45 2023-03-16 21:30:33 2023-03-16 21:35:08  275.0  B1    137282     0   
46 2023-03-16 21:30:33 2023-03-16 21:35:08  276.0  B7    136378     0   
47 2023-03-16 21:30:33 2023-03-16 21:35:08  276.0  B8    137214     0   

         PLR  rx_count  excl       ELR     PLELR     avg_L     min_L  \
0   0.022858    139961  3432  2.452112  2.474409  0.024638  0.008942   
1   0.155008    139776   337  0.241100  0.395734  0.010944  0.005662   
2   0.947190    138667   228  0.164423  1.110056  0.011160  0.005629   
3   0.000000    137494   349  0.253829  0.253829  0.013291  0.008500   
4   2.214642    134449   480  0.357013  2.563748  0.011733  0.006204   
5   0.1

## Dual Radio

In [76]:
def get_dr_stats(df, BID):
    if df.empty:
        return pd.DataFrame()
    df = df.head(-1).tail(-1).reset_index(drop=True)
    df = df.drop(columns=['PCI_m','EARFCN_m','nrPCI_m','nrARFCN_m',
                        'PCI_s','EARFCN_s','nrPCI_s','nrARFCN_s',
                        'ho_type','ho_type1','ho_type2'])
    df_stats = pd.DataFrame()
    df_stats.at[0, 'start'] = df.iloc[0]['Timestamp']
    df_stats.at[0, 'end'] = df.iloc[-1]['Timestamp']
    df_stats.at[0, 'time'] = len(df)
    df_stats.at[0, 'BID'] = BID

    df_stats = pd.concat([df_stats, df[['tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
                                        'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
                                        'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L']].mean().to_frame().T], axis=1)
    df_stats['tx_count'] = df['tx_count'].sum()
    df_stats['lost_ms'] = df['lost_ms'].sum()
    df_stats['lost_mlss'] = df['lost_mlss'].sum()
    df_stats['rx_count'] = df['rx_count'].sum()
    df_stats['excl_ms'] = df['excl_ms'].sum()
    df_stats['excl_mess'] = df['excl_mess'].sum()
    df_stats['PLR_ms'] = df_stats['lost_ms'] / df_stats['tx_count'] * 100
    df_stats['PLR_mlss'] = df_stats['lost_mlss'] / df_stats['tx_count'] * 100
    df_stats['ELR_ms'] = df_stats['excl_ms'] / df_stats['rx_count'] * 100
    df_stats['ELR_mess'] = df_stats['excl_mess'] / df_stats['rx_count'] * 100
    df_stats['PLELR_ms'] = (df_stats['lost_ms'] + df_stats['excl_ms']) / df_stats['tx_count'] * 100
    df_stats['PLELR_mless'] = (df_stats['lost_mlss'] + df_stats['excl_mess']) / df_stats['tx_count'] * 100

    for tag in df.columns:
        if tag.startswith(('RSRP','RSRQ','nrRSRP','nrRSRQ')):
            df_stats.at[0, tag] = df[tag].mean()
            df_stats.at[0, f'jitter_{tag}'] = df[tag].diff().abs().mean()

    df_stats = pd.concat([df_stats, df.drop(columns=['Timestamp','tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
                                                    'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
                                                    'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
                                                    'RSRP_m','RSRQ_m','nrRSRP_m','nrRSRQ_m',
                                                    'RSRP_s','RSRQ_s','nrRSRP_s','nrRSRQ_s',
                                                    'RSRP_ms','RSRQ_ms','nrRSRP_ms','nrRSRQ_ms']).sum().to_frame().T], axis=1)
    df_stats.at[0, 'st_scel_m'] = df.loc[df['st_scel_m'] != 0, 'st_scel_m'].mean()
    df_stats.at[0, 'st_scel_s'] = df.loc[df['st_scel_s'] != 0, 'st_scel_s'].mean()
    
    return df_stats

In [77]:
print(schemes)
xs = list(it.combinations(range(len(schemes)), 2))
xs = [schemes[x[0]]+'+'+schemes[x[1]] for x in xs]
print(xs)

['B1', 'B7', 'B8']
['B1+B7', 'B1+B8', 'B7+B8']


In [78]:
N = len(dfaggs_ul_dr)
table_ul_dr = pd.DataFrame()

for i in range(N):
    for j, x in enumerate(xs):
        df = dfaggs_ul_dr[i][j]
        table_ul_dr = pd.concat([table_ul_dr, get_dr_stats(df, x)])
table_ul_dr = table_ul_dr.sort_values(by=['start', 'BID']).reset_index(drop=True)
display(table_ul_dr)
table_ul_dr.to_pickle('table_ul_dr_stats.pkl')

start                 end   time    BID  tx_count  lost_ms  \
0  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B1+B7    137493        3   
1  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B1+B8    137493        0   
2  2023-03-15 15:19:19 2023-03-15 15:23:53  275.0  B7+B8    137493        4   
3  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B1+B7    138993        0   
4  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B1+B8    138993        0   
5  2023-03-15 15:58:33 2023-03-15 16:03:10  278.0  B7+B8    138993        0   
6  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B1+B7    132994        0   
7  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B1+B8    132994        0   
8  2023-03-15 16:17:32 2023-03-15 16:21:57  266.0  B7+B8    132994        2   
9  2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B1+B7    136993        0   
10 2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B1+B8    136993        0   
11 2023-03-15 16:57:32 2023-03-15 17:02:05  274.0  B7+B8    136993        0   
12 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B1+B7    140493        0   
13 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B1+B8    140493        0   
14 2023-03-16 19:23:53 2023-03-16 19:28:33  281.0  B7+B8    140493        0   
15 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1+B7    137494        0   
16 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1+B8    137494        0   
17 2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B7+B8    137494        0   
18 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1+B7    143494        0   
19 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1+B8    143494        0   
20 2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B7+B8    143494        0   
21 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1+B7    135494        0   
22 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1+B8    135494        0   
23 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B7+B8    135494        1   
24 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1+B7    138493        0   
25 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1+B8    138493        0   
26 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B7+B8    138493        0   
27 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1+B7    136493        0   
28 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1+B8    136493        0   
29 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B7+B8    136493        0   
30 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1+B7    133494        0   
31 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1+B8    133494        0   
32 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B7+B8    133494        0   
33 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1+B7    134994        0   
34 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1+B8    134994        0   
35 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B7+B8    134994       10   
36 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B1+B7    140494        0   
37 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B1+B8    140494        0   
38 2023-03-16 20:26:51 2023-03-16 20:31:31  281.0  B7+B8    140494        0   
39 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1+B7    136493        0   
40 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1+B8    136493        0   
41 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B7+B8    136493        2   
42 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1+B7    135493        0   
43 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1+B8    135493        0   
44 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B7+B8    135493        4   
45 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1+B7    133994        0   
46 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1+B8    133994        0   
47 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B7+B8    133994        0   

      PLR_ms  lost_mlss  PLR_mlss  rx_count  excl_ms    ELR_ms  PLELR_ms  \
0   0.002182        148  0.107642    137490        0  0.000000  0.002

In [79]:
N = len(dfaggs_dl_dr)
table_dl_dr = pd.DataFrame()

for i in range(N):
    for j, x in enumerate(xs):
        df = dfaggs_dl_dr[i][j]
        table_dl_dr = pd.concat([table_dl_dr, get_dr_stats(df, x)])
table_dl_dr = table_dl_dr.sort_values(by=['start', 'BID']).reset_index(drop=True)
display(table_dl_dr)
table_dl_dr.to_pickle('table_dl_dr_stats.pkl')

start                 end   time    BID  tx_count  lost_ms  \
0  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B1+B7    139993        0   
1  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B1+B8    139993        0   
2  2023-03-16 19:23:54 2023-03-16 19:28:33  280.0  B7+B8    139993        0   
3  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1+B7    137494        0   
4  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B1+B8    137494        0   
5  2023-03-16 19:32:54 2023-03-16 19:37:28  275.0  B7+B8    137494       11   
6  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1+B7    143494        0   
7  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B1+B8    143494        0   
8  2023-03-16 19:38:58 2023-03-16 19:43:44  287.0  B7+B8    143494        0   
9  2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1+B7    135494        0   
10 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B1+B8    135494        0   
11 2023-03-16 19:47:54 2023-03-16 19:52:24  271.0  B7+B8    135494        0   
12 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1+B7    138494        0   
13 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B1+B8    138494        0   
14 2023-03-16 19:55:53 2023-03-16 20:00:29  277.0  B7+B8    138494        0   
15 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1+B7    136494        0   
16 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B1+B8    136494        0   
17 2023-03-16 20:03:54 2023-03-16 20:08:26  273.0  B7+B8    136494      133   
18 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1+B7    133494        0   
19 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B1+B8    133494        0   
20 2023-03-16 20:09:41 2023-03-16 20:14:07  267.0  B7+B8    133494      440   
21 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1+B7    134994        0   
22 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B1+B8    134994        0   
23 2023-03-16 20:18:15 2023-03-16 20:22:44  270.0  B7+B8    134994        0   
24 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B1+B7    139993      614   
25 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B1+B8    139993      142   
26 2023-03-16 20:26:52 2023-03-16 20:31:31  280.0  B7+B8    139993      142   
27 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1+B7    136494        0   
28 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B1+B8    136494        0   
29 2023-03-16 20:33:41 2023-03-16 20:38:13  273.0  B7+B8    136494        1   
30 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1+B7    135494        0   
31 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B1+B8    135494        0   
32 2023-03-16 20:42:38 2023-03-16 20:47:08  271.0  B7+B8    135494        0   
33 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1+B7    133994        0   
34 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B1+B8    133994      303   
35 2023-03-16 20:49:14 2023-03-16 20:53:41  268.0  B7+B8    133994       15   
36 2023-03-16 20:59:06 2023-03-16 21:03:37  270.0  B1+B7    134142        0   
37 2023-03-16 20:59:06 2023-03-16 21:03:37  270.0  B1+B8    134479        0   
38 2023-03-16 20:59:06 2023-03-16 21:03:37  272.0  B7+B8    135430        0   
39 2023-03-16 21:09:56 2023-03-16 21:14:27  271.0  B1+B7    134860        0   
40 2023-03-16 21:09:56 2023-03-16 21:14:27  272.0  B1+B8    135351        0   
41 2023-03-16 21:09:56 2023-03-16 21:14:27  271.0  B7+B8    134218        0   
42 2023-03-16 21:20:53 2023-03-16 21:25:17  264.0  B1+B7    131084        0   
43 2023-03-16 21:20:53 2023-03-16 21:25:17  264.0  B1+B8    131590        0   
44 2023-03-16 21:20:53 2023-03-16 21:25:17  263.0  B7+B8    130289        0   
45 2023-03-16 21:30:33 2023-03-16 21:35:08  275.0  B1+B7    135667        0   
46 2023-03-16 21:30:33 2023-03-16 21:35:08  275.0  B1+B8    136639        0   
47 2023-03-16 21:30:33 2023-03-16 21:35:08  276.0  B7+B8    135600        0   

      PLR_ms  lost_mlss  PLR_mlss  rx_count  excl_ms    ELR_ms  PLELR_ms  \
0   0.000000         32  0.022858    139993        0  0.000000  0.000

# Regression

In [1]:
import pandas as pd
import numpy as np
import statsmodels.api as sm
import statsmodels.formula.api as smf

# display(table_ul_sr.head())
# display(table_dl_sr.head())
# display(table_ul_dr.head())
# display(table_dl_dr.head())

In [ ]:
handover_type = ['stable',
                 'LTE_HO','MN_HO','SN_HO','MNSN_HO','SN_Rel','SN_Setup','SN_Rel_MN_HO','SN_Setup_MN_HO',
                 'SCG_Failure_t310-Expiry (0)','SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)','SCG_Failure_synchReconfigFailureSCG (3)',
                 'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                 'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                 'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
handover_type1 = ['stable','sn_change','intra_freq','inter_freq']
handover_type2 = ['stable','sn_change','intra_sector','inter_sector','inter_enb','unknown_enb']

handover_type = list(it.product(handover_type, repeat=2))
handover_type = ['+'.join([s[0],s[1]]) for s in handover_type][1:]
handover_type1 = list(it.product(handover_type1, repeat=2))
handover_type1 = ['+'.join([s[0],s[1]]) for s in handover_type1][1:]
handover_type1 = [s for s in handover_type1 if not np.in1d(s, ['stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])]
handover_type2 = list(it.product(handover_type2, repeat=2))
handover_type2 = ['+'.join([s[0],s[1]]) for s in handover_type2][1:]
handover_type2 = [s for s in handover_type2 if not np.in1d(s, ['stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])]

print(handover_type)
print(handover_type1)
print(handover_type2)

['stable+LTE_HO', 'stable+MN_HO', 'stable+SN_HO', 'stable+MNSN_HO', 'stable+SN_Rel', 'stable+SN_Setup', 'stable+SN_Rel_MN_HO', 'stable+SN_Setup_MN_HO', 'stable+SCG_Failure_t310-Expiry (0)', 'stable+SCG_Failure_randomAccessProblem (1)', 'stable+SCG_Failure_rlc-MaxNumRetx (2)', 'stable+SCG_Failure_synchReconfigFailureSCG (3)', 'stable+SCG_Failure_scg-ReconfigFailure (4)', 'stable+SCG_Failure_srb3-IntegrityFailure (5)', 'stable+SCG_Failure_other-r16 (6)', 'stable+MCG_Failure_reconfigurationFailure (0)', 'stable+MCG_Failure_handoverFailure (1)', 'stable+MCG_Failure_otherFailure (2)', 'stable+NAS_Recovery_reconfigurationFailure (0)', 'stable+NAS_Recovery_handoverFailure (1)', 'stable+NAS_Recovery_otherFailure (2)', 'LTE_HO+stable', 'LTE_HO+LTE_HO', 'LTE_HO+MN_HO', 'LTE_HO+SN_HO', 'LTE_HO+MNSN_HO', 'LTE_HO+SN_Rel', 'LTE_HO+SN_Setup', 'LTE_HO+SN_Rel_MN_HO', 'LTE_HO+SN_Setup_MN_HO', 'LTE_HO+SCG_Failure_t310-Expiry (0)', 'LTE_HO+SCG_Failure_randomAccessProblem (1)', 'LTE_HO+SCG_Failure_rlc-MaxN

## dual Uplink

In [ ]:
df = table_ul_dr.copy()
df = df.drop(columns=['stable+stable', 'stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])
df = df.drop(columns=handover_type1)
df = df.drop(columns=handover_type2)
### Select Features
y = df['PLR_ms']
X = df.drop(columns=[
    ## label
    'start','end','time','BID',
    ## candidate y
    'tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
    'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
    'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
    ## candidate X
    'RSRP_m','jitter_RSRP_m','RSRQ_m','jitter_RSRQ_m','nrRSRP_m','jitter_nrRSRP_m','nrRSRQ_m','jitter_nrRSRQ_m',
    'RSRP_s','jitter_RSRP_s','RSRQ_s','jitter_RSRQ_s','nrRSRP_s','jitter_nrRSRP_s','nrRSRQ_s','jitter_nrRSRQ_s',
    'RSRP_ms','jitter_RSRP_ms','RSRQ_ms','jitter_RSRQ_ms','nrRSRP_ms','jitter_nrRSRP_ms','nrRSRQ_ms','jitter_nrRSRQ_ms',
    'ho_num_m','ho_num_s',
    'ho_num_ms',
    'st_scel_m','st_scel_s',
    'mnpp_m','mnpp_s','snpp_m','snpp_s'
]).copy()
X = sm.add_constant(X)
X = X.astype(float)
y = y.astype(float)

display(y)
# display(X)

### Regression: Hopes p.value < 0.1/0.05/0.01
model = sm.OLS(y, X).fit()
print(model.summary())

0     0.002182
1     0.000000
2     0.002909
3     0.000000
4     0.000000
5     0.000000
6     0.000000
7     0.000000
8     0.001504
9     0.000000
10    0.000000
11    0.000000
12    0.000000
13    0.000000
14    0.000000
15    0.000000
16    0.000000
17    0.000000
18    0.000000
19    0.000000
20    0.000000
21    0.000000
22    0.000000
23    0.000738
24    0.000000
25    0.000000
26    0.000000
27    0.000000
28    0.000000
29    0.000000
30    0.000000
31    0.000000
32    0.000000
33    0.000000
34    0.000000
35    0.007408
36    0.000000
37    0.000000
38    0.000000
39    0.000000
40    0.000000
41    0.001465
42    0.000000
43    0.000000
44    0.002952
45    0.000000
46    0.000000
47    0.000000
Name: PLR_ms, dtype: float64

                            OLS Regression Results                            
Dep. Variable:                 PLR_ms   R-squared:                       0.960
Model:                            OLS   Adj. R-squared:                  0.765
Method:                 Least Squares   F-statistic:                     4.920
Date:                Fri, 24 Mar 2023   Prob (F-statistic):             0.0114
Time:                        21:50:36   Log-Likelihood:                 330.28
No. Observations:                  48   AIC:                            -580.6
Df Residuals:                       8   BIC:                            -505.7
Df Model:                          39                                         
Covariance Type:            nonrobust                                         
                                                                                      coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------

## dual Downlink

In [ ]:
handover_type = ['stable',
                 'LTE_HO','MN_HO','SN_HO', # 'MNSN_HO',
                 'SN_Rel','SN_Setup', # 'SN_Rel_MN_HO','SN_Setup_MN_HO',
                 'SCG_Failure_t310-Expiry (0)', # 'SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)',
                 'SCG_Failure_synchReconfigFailureSCG (3)',
                 # 'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                 'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                 'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
handover_type = list(it.product(handover_type, repeat=2))
handover_type = ['+'.join([s[0],s[1]]) for s in handover_type][1:]

df = table_dl_dr.copy()
df = df.drop(columns=['stable+stable', 'stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])
df = df.drop(columns=handover_type1)
df = df.drop(columns=handover_type2)
### Select Features
y = df['PLR_ms']
X = df.drop(columns=[
    ## label
    'start','end','time','BID',
    ## candidate y
    'tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
    'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
    'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
    ## candidate X
    'RSRP_m','jitter_RSRP_m','RSRQ_m','jitter_RSRQ_m','nrRSRP_m','jitter_nrRSRP_m','nrRSRQ_m','jitter_nrRSRQ_m',
    'RSRP_s','jitter_RSRP_s','RSRQ_s','jitter_RSRQ_s','nrRSRP_s','jitter_nrRSRP_s','nrRSRQ_s','jitter_nrRSRQ_s',
    'RSRP_ms','jitter_RSRP_ms','RSRQ_ms','jitter_RSRQ_ms','nrRSRP_ms','jitter_nrRSRP_ms','nrRSRQ_ms','jitter_nrRSRQ_ms',
    'ho_num_m','ho_num_s',
    'ho_num_ms',
    'st_scel_m','st_scel_s',
    'mnpp_m','mnpp_s','snpp_m','snpp_s'
]).copy()
X = df[handover_type].copy()

X = sm.add_constant(X)
X = X.astype(float)
y = y.astype(float)

# display(y)
# display(X)

### Regression: Hopes p.value < 0.1/0.05/0.01
model = sm.OLS(y, X).fit()
print(model.summary())

### p-values
# pvalues = model.pvalues.iloc[1:]
# pvalues_sorted = pvalues.sort_values()
# with pd.option_context('display.max_rows', None):
#     print(pvalues_sorted)

                            OLS Regression Results                            
Dep. Variable:                 PLR_ms   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                  1.000
Method:                 Least Squares   F-statistic:                 6.382e+27
Date:                Sun, 26 Mar 2023   Prob (F-statistic):          1.85e-124
Time:                        22:55:49   Log-Likelihood:                 1621.4
No. Observations:                  48   AIC:                            -3165.
Df Residuals:                       9   BIC:                            -3092.
Df Model:                          38                                         
Covariance Type:            nonrobust                                         
                                                                                      coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------

In [ ]:
df = table_dl_dr.copy()
df = df.drop(columns=['stable+stable', 'stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])
df = df.drop(columns=handover_type1)
df = df.drop(columns=handover_type2)

df = df.drop(columns=[
    ## label
    'start','end','time','BID',
    ## candidate y
    'tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
    'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
    'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
    ## candidate X
    'RSRP_m','jitter_RSRP_m','RSRQ_m','jitter_RSRQ_m','nrRSRP_m','jitter_nrRSRP_m','nrRSRQ_m','jitter_nrRSRQ_m',
    'RSRP_s','jitter_RSRP_s','RSRQ_s','jitter_RSRQ_s','nrRSRP_s','jitter_nrRSRP_s','nrRSRQ_s','jitter_nrRSRQ_s',
    'RSRP_ms','jitter_RSRP_ms','RSRQ_ms','jitter_RSRQ_ms','nrRSRP_ms','jitter_nrRSRP_ms','nrRSRQ_ms','jitter_nrRSRQ_ms',
    'ho_num_m','ho_num_s',
    'ho_num_ms',
    'st_scel_m','st_scel_s',
    'mnpp_m','mnpp_s','snpp_m','snpp_s'
]).copy()

In [ ]:
with pd.option_context('display.max_rows', None):
    print(df.sum().sort_values(ascending=False))

stable+MN_HO                                                                       648
stable+SN_HO                                                                       636
LTE_HO+stable                                                                      319
MN_HO+stable                                                                       195
SN_HO+stable                                                                       177
stable+SN_Setup                                                                    137
LTE_HO+MN_HO                                                                       104
LTE_HO+SN_HO                                                                        96
stable+LTE_HO                                                                       91
stable+MCG_Failure_otherFailure (2)                                                 59
SN_Setup+stable                                                                     54
MCG_Failure_otherFailure (2)+stable        

# New Regression

In [163]:
import pandas as pd
import numpy as np
import statsmodels.api as sm
import statsmodels.formula.api as smf

table_ul_sr = pd.read_pickle('table_ul_sr_stats.pkl')
table_dl_sr = pd.read_pickle('table_dl_sr_stats.pkl')
table_ul_dr = pd.read_pickle('table_ul_dr_stats.pkl')
table_dl_dr = pd.read_pickle('table_dl_dr_stats.pkl')

# display(table_ul_sr.head())
# display(table_dl_sr.head())
# display(table_ul_dr.head())
# display(table_dl_dr.head())

def get_dr_stats(df, BID):
    if df.empty:
        return pd.DataFrame()
    df = df.head(-1).tail(-1).reset_index(drop=True)
    df = df.drop(columns=['PCI_m','EARFCN_m','nrPCI_m','nrARFCN_m',
                        'PCI_s','EARFCN_s','nrPCI_s','nrARFCN_s',
                        'ho_type','ho_type1','ho_type2'])
    df_stats = pd.DataFrame()
    df_stats.at[0, 'start'] = df.iloc[0]['Timestamp']
    df_stats.at[0, 'end'] = df.iloc[-1]['Timestamp']
    df_stats.at[0, 'time'] = len(df)
    df_stats.at[0, 'BID'] = BID

    df_stats = pd.concat([df_stats, df[['tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
                                        'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
                                        'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L']].mean().to_frame().T], axis=1)
    df_stats['tx_count'] = df['tx_count'].sum()
    df_stats['lost_ms'] = df['lost_ms'].sum()
    df_stats['lost_mlss'] = df['lost_mlss'].sum()
    df_stats['rx_count'] = df['rx_count'].sum()
    df_stats['excl_ms'] = df['excl_ms'].sum()
    df_stats['excl_mess'] = df['excl_mess'].sum()
    df_stats['PLR_ms'] = df_stats['lost_ms'] / df_stats['tx_count'] * 100
    df_stats['PLR_mlss'] = df_stats['lost_mlss'] / df_stats['tx_count'] * 100
    df_stats['ELR_ms'] = df_stats['excl_ms'] / df_stats['rx_count'] * 100
    df_stats['ELR_mess'] = df_stats['excl_mess'] / df_stats['rx_count'] * 100
    df_stats['PLELR_ms'] = (df_stats['lost_ms'] + df_stats['excl_ms']) / df_stats['tx_count'] * 100
    df_stats['PLELR_mless'] = (df_stats['lost_mlss'] + df_stats['excl_mess']) / df_stats['tx_count'] * 100

    for tag in df.columns:
        if tag.startswith(('RSRP','RSRQ','nrRSRP','nrRSRQ')):
            df_stats.at[0, tag] = df[tag].mean()
            df_stats.at[0, f'jitter_{tag}'] = df[tag].diff().abs().mean()

    df_stats = pd.concat([df_stats, df.drop(columns=['Timestamp','tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
                                                    'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
                                                    'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
                                                    'RSRP_m','RSRQ_m','nrRSRP_m','nrRSRQ_m',
                                                    'RSRP_s','RSRQ_s','nrRSRP_s','nrRSRQ_s',
                                                    'RSRP_ms','RSRQ_ms','nrRSRP_ms','nrRSRQ_ms']).sum().to_frame().T], axis=1)
    df_stats.at[0, 'st_scel_m'] = df.loc[df['st_scel_m'] != 0, 'st_scel_m'].mean()
    df_stats.at[0, 'st_scel_s'] = df.loc[df['st_scel_s'] != 0, 'st_scel_s'].mean()
    
    return df_stats

In [164]:
# handover_type = ['stable',
#                  'LTE_HO','MN_HO','SN_HO','MNSN_HO','SN_Rel','SN_Setup','SN_Rel_MN_HO','SN_Setup_MN_HO',
#                  'SCG_Failure_t310-Expiry (0)','SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)','SCG_Failure_synchReconfigFailureSCG (3)',
#                  'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
#                  'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
#                  'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
handover_type = ['stable',
                 'LTE_HO','MN_HO','SN_HO', # 'MNSN_HO',
                 'SN_Rel','SN_Setup', # 'SN_Rel_MN_HO','SN_Setup_MN_HO',
                 'SCG_Failure_t310-Expiry (0)', # 'SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)',
                 'SCG_Failure_synchReconfigFailureSCG (3)',
                 # 'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                 'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                 'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']
handover_type1 = ['stable','sn_change','intra_freq','inter_freq']
handover_type2 = ['stable','sn_change','intra_sector','inter_sector','inter_enb','unknown_enb']

handover_type = list(it.product(handover_type, repeat=2))
handover_type = ['+'.join([s[0],s[1]]) for s in handover_type][1:]
handover_type1 = list(it.product(handover_type1, repeat=2))
handover_type1 = ['+'.join([s[0],s[1]]) for s in handover_type1][1:]
handover_type1 = [s for s in handover_type1 if not np.in1d(s, ['stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])]
handover_type2 = list(it.product(handover_type2, repeat=2))
handover_type2 = ['+'.join([s[0],s[1]]) for s in handover_type2][1:]
handover_type2 = [s for s in handover_type2 if not np.in1d(s, ['stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])]

print(handover_type)
print(handover_type1)
print(handover_type2)

['stable+LTE_HO', 'stable+MN_HO', 'stable+SN_HO', 'stable+SN_Rel', 'stable+SN_Setup', 'stable+SCG_Failure_t310-Expiry (0)', 'stable+SCG_Failure_synchReconfigFailureSCG (3)', 'stable+MCG_Failure_reconfigurationFailure (0)', 'stable+MCG_Failure_handoverFailure (1)', 'stable+MCG_Failure_otherFailure (2)', 'stable+NAS_Recovery_reconfigurationFailure (0)', 'stable+NAS_Recovery_handoverFailure (1)', 'stable+NAS_Recovery_otherFailure (2)', 'LTE_HO+stable', 'LTE_HO+LTE_HO', 'LTE_HO+MN_HO', 'LTE_HO+SN_HO', 'LTE_HO+SN_Rel', 'LTE_HO+SN_Setup', 'LTE_HO+SCG_Failure_t310-Expiry (0)', 'LTE_HO+SCG_Failure_synchReconfigFailureSCG (3)', 'LTE_HO+MCG_Failure_reconfigurationFailure (0)', 'LTE_HO+MCG_Failure_handoverFailure (1)', 'LTE_HO+MCG_Failure_otherFailure (2)', 'LTE_HO+NAS_Recovery_reconfigurationFailure (0)', 'LTE_HO+NAS_Recovery_handoverFailure (1)', 'LTE_HO+NAS_Recovery_otherFailure (2)', 'MN_HO+stable', 'MN_HO+LTE_HO', 'MN_HO+MN_HO', 'MN_HO+SN_HO', 'MN_HO+SN_Rel', 'MN_HO+SN_Setup', 'MN_HO+SCG_Fai

In [174]:
# df = df.drop(columns=['stable+stable', 'stable+sn_change', 'sn_change+stable', 'sn_change+sn_change'])
# df = df.drop(columns=handover_type1)
# df = df.drop(columns=handover_type2)
### Select Features
# X = df.drop(columns=[
#     ## label
#     'start','end','time','BID',
#     ## candidate y
#     'tx_count','lost_ms','PLR_ms','lost_mlss','PLR_mlss',
#     'rx_count','excl_ms','ELR_ms','PLELR_ms','excl_mess','ELR_mess','PLELR_mless',
#     'avg_L','min_L','max_L','median_L','std_L','var_L','jitter_L',
#     ## candidate X
#     'RSRP_m','jitter_RSRP_m','RSRQ_m','jitter_RSRQ_m','nrRSRP_m','jitter_nrRSRP_m','nrRSRQ_m','jitter_nrRSRQ_m',
#     'RSRP_s','jitter_RSRP_s','RSRQ_s','jitter_RSRQ_s','nrRSRP_s','jitter_nrRSRP_s','nrRSRQ_s','jitter_nrRSRQ_s',
#     'RSRP_ms','jitter_RSRP_ms','RSRQ_ms','jitter_RSRQ_ms','nrRSRP_ms','jitter_nrRSRP_ms','nrRSRQ_ms','jitter_nrRSRQ_ms',
#     'ho_num_m','ho_num_s',
#     'ho_num_ms',
#     'st_scel_m','st_scel_s',
#     'mnpp_m','mnpp_s','snpp_m','snpp_s'
# ]).copy()

handover_type = ['stable',
                 'LTE_HO','MN_HO','SN_HO', # 'MNSN_HO',
                 'SN_Rel','SN_Setup', # 'SN_Rel_MN_HO','SN_Setup_MN_HO',
                 'SCG_Failure_t310-Expiry (0)', # 'SCG_Failure_randomAccessProblem (1)','SCG_Failure_rlc-MaxNumRetx (2)',
                 'SCG_Failure_synchReconfigFailureSCG (3)',
                 # 'SCG_Failure_scg-ReconfigFailure (4)','SCG_Failure_srb3-IntegrityFailure (5)','SCG_Failure_other-r16 (6)',
                 'MCG_Failure_reconfigurationFailure (0)','MCG_Failure_handoverFailure (1)','MCG_Failure_otherFailure (2)',
                 'NAS_Recovery_reconfigurationFailure (0)','NAS_Recovery_handoverFailure (1)','NAS_Recovery_otherFailure (2)']

handover_type = list(it.product(handover_type, repeat=2))
handover_type = ['+'.join([s[0],s[1]]) for s in handover_type][1:]

df = table_dl_dr.copy()

X = df[['RSRP_ms', 'RSRQ_ms', 'nrRSRP_ms', 'nrRSRQ_ms', *handover_type]].copy()
X = sm.add_constant(X)
X = X.astype(float)

y = df['PLR_ms']
y = y.astype(float)

### Regression: Hopes p.value < 0.1/0.05/0.01
model = sm.OLS(y.head(-3).copy(), X.head(-3).copy()).fit()
print(model.summary())

### Get p-values
d = {}
for i in X.columns.tolist():
    d[f'{i}'] = model.pvalues[i]
print(d)
# df_pvalue = pd.DataFrame(d.items(), columns=['Var_name', 'p-Value']).sort_values(by = 'p-Value').reset_index(drop=True)
df_pvalue = pd.DataFrame(d.items(), columns=['Var_name', 'p-Value'])
df_pvalue = df_pvalue[df_pvalue['p-Value'] < 0.05]
with pd.option_context('display.max_rows', None):
    display(df_pvalue)
df_pvalue.to_csv('pvalue.csv', index=False)

                            OLS Regression Results                            
Dep. Variable:                 PLR_ms   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                  1.000
Method:                 Least Squares   F-statistic:                 7.711e+26
Date:                Mon, 27 Mar 2023   Prob (F-statistic):           6.57e-41
Time:                        20:24:31   Log-Likelihood:                 1497.6
No. Observations:                  45   AIC:                            -2911.
Df Residuals:                       3   BIC:                            -2835.
Df Model:                          41                                         
Covariance Type:            nonrobust                                         
                                                                                      coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------

Var_name       p-Value
12       stable+MCG_Failure_reconfigurationFailure (0)  1.123945e-31
15      stable+NAS_Recovery_reconfigurationFailure (0)  9.340968e-30
16             stable+NAS_Recovery_handoverFailure (1)  6.158153e-30
17                stable+NAS_Recovery_otherFailure (2)  7.697143e-39
24                  LTE_HO+SCG_Failure_t310-Expiry (0)  2.254378e-33
26       LTE_HO+MCG_Failure_reconfigurationFailure (0)  2.921110e-28
27              LTE_HO+MCG_Failure_handoverFailure (1)  2.817774e-32
29      LTE_HO+NAS_Recovery_reconfigurationFailure (0)  6.217056e-33
30             LTE_HO+NAS_Recovery_handoverFailure (1)  3.934870e-32
31                LTE_HO+NAS_Recovery_otherFailure (2)  1.456792e-33
32                                        MN_HO+stable  5.082769e-36
33                                        MN_HO+LTE_HO  1.731836e-37
34                                         MN_HO+MN_HO  2.894695e-40
35                                         MN_HO+SN_HO  6.694317e-37
36                                        MN_HO+SN_Rel  5.564987e-34
37                                      MN_HO+SN_Setup  1.731836e-37
38                   MN_HO+SCG_Failure_t310-Expiry (0)  6.142860e-38
39       MN_HO+SCG_Failure_synchReconfigFailureSCG (3)  2.693564e-37
40        MN_HO+MCG_Failure_reconfigurationFailure (0)  1.356803e-37
41               MN_HO+MCG_Failure_handoverFailure (1)  5.736836e-37
42                  MN_HO+MCG_Failure_otherFailure (2)  5.736836e-37
43       MN_HO+NAS_Recovery_reconfigurationFailure (0)  5.736836e-37
46                                        SN_HO+stable  1.533365e-37
47                                        SN_HO+LTE_HO  2.029005e-38
48                                         SN_HO+MN_HO  6.676021e-39
49                                         SN_HO+SN_HO  1.008742e-38
51                                      SN_HO+SN_Setup  1.690561e-39
56                  SN_HO+MCG_Failure_otherFailure (2)  2.671144e-36
60                                       SN_Rel+stable  4.044825e-37
62                                        SN_Rel+MN_HO  1.091288e-40
63                                        SN_Rel+SN_HO  1.731836e-37
70                 SN_Rel+MCG_Failure_otherFailure (2)  1.731836e-37
74                                     SN_Setup+stable  3.829322e-37
75                                     SN_Setup+LTE_HO  2.816783e-41
76                                      SN_Setup+MN_HO  3.902383e-37
77                                      SN_Setup+SN_HO  1.129341e-36
79                                   SN_Setup+SN_Setup  1.061999e-36
84               SN_Setup+MCG_Failure_otherFailure (2)  2.931624e-40
91                   SCG_Failure_t310-Expiry (0)+SN_HO  9.650090e-41
102     SCG_Failure_synchReconfigFailureSCG (3)+stable  4.044825e-37
104      SCG_Failure_synchReconfigFailureSCG (3)+MN_HO  1.091288e-40
131             MCG_Failure_handoverFailure (1)+LTE_HO  1.731836e-37
133              MCG_Failure_handoverFailure (1)+SN_HO  1.731836e-37
135           MCG_Failure_handoverFailure (1)+SN_Setup  1.731836e-37
140  MCG_Failure_handoverFailure (1)+MCG_Failure_ot...  3.585767e-39
145                MCG_Failure_otherFailure (2)+LTE_HO  9.650090e-41
147                 MCG_Failure_otherFailure (2)+SN_HO  9.116281e-37
149              MCG_Failure_otherFailure (2)+SN_Setup  9.105713e-42
154  MCG_Failure_otherFailure (2)+MCG_Failure_other...  4.036640e-41

In [167]:
ypred = model.predict(X.tail(3))
pprint(list(zip(y.tail(3), ypred)))

[(0.0, -3.0383398558723533e-16),
 (0.0, -3.9331164273604185e-16),
 (0.0, 0.1609967757069352)]


In [158]:
import random
# x = random.choice([0,1,2])
N = len(dfaggs_dl_dr[12][0]) // 30
dic = {0:'B1+B7',1:'B1+B8',2:'B7+B8'}

for x in [0,1,2]:
    df_ = pd.DataFrame()
    for i in range(N+1):
        if i < N:
            j = i*30
            k = (i+1)*30
        else:
            j = i*30
            k = len(dfaggs_dl_dr[12][0])
        print(x, dic[x])
        df = dfaggs_dl_dr[12][x].copy().iloc[j:k]
        df_ = pd.concat([df_, df])
        
        X = get_dr_stats(df, '0')
        X = X[['RSRP_ms', 'RSRQ_ms', 'nrRSRP_ms', 'nrRSRQ_ms', *handover_type]].copy()
        X['const'] = 1
        X = X.astype(float)
        ypred = model.predict(X)
        
        print(ypred[0])
        if ypred[0] > 5e-2:
            x = random.choice([s for s in [0,1,2] if s != x])

    result = get_dr_stats(df_, '0')
    print('result:', result.at[0, 'PLR_ms'])
    print('benchmark B1+B7:', table_dl_dr.at[24, 'PLR_ms'])
    print('benchmark B1+B8:', table_dl_dr.at[25, 'PLR_ms'])
    print('benchmark B7+B8:', table_dl_dr.at[26, 'PLR_ms'])
    print()

0 B1+B7
0.056721816868281406
2 B7+B8
0.08918386970390575
1 B1+B8
0.11344363373652668
2 B7+B8
-0.08854398560660041
2 B7+B8
3.5340565456010465e-14
2 B7+B8
-0.02425976403258748
2 B7+B8
3.272858079623436e-14
2 B7+B8
0.10102156889320164
1 B1+B8
3.1249826109247793e-14
1 B1+B8
3.6306210335222724e-14
result: 0.10143364311072697
benchmark B1+B7: 0.4385933582393405
benchmark B1+B8: 0.10143364311072697
benchmark B7+B8: 0.10143364311072697

1 B1+B8
3.6202028672056266e-14
1 B1+B8
0.11344363373652515
2 B7+B8
0.05672181686828648
1 B1+B8
3.362389551369439e-14
1 B1+B8
3.429001282345318e-14
1 B1+B8
3.525584033579956e-14
1 B1+B8
3.1639992011818644e-14
1 B1+B8
0.11344363373652996
0 B1+B7
3.2499926643579284e-14
0 B1+B7
3.6892766169687996e-14
result: 0.10143364311072697
benchmark B1+B7: 0.4385933582393405
benchmark B1+B8: 0.10143364311072697
benchmark B7+B8: 0.10143364311072697

2 B7+B8
0.03246205283566561
2 B7+B8
0.08918386970390575
0 B1+B7
0.05672181686828247
2 B7+B8
-0.08854398560660041
2 B7+B8
3.5340565